In [1]:
import os
import requests
import json
import folium
import pandas as pd
import numpy as np
import geopandas as gpd
import zipfile

In [2]:
zipcodes = pd.read_csv('JP_zip.csv')

zipcodes = zipcodes.rename(columns={'zip_code':'zipcode'})

### Only grab the data from Tokyo...
tokyo = zipcodes[zipcodes.State_province == 'Toukyouto']

### Convert zipcodes from "XXX-YYYY" to XXXYYYY
tokyo = tokyo.assign(zipcode = tokyo.zipcode.apply(lambda x: x.replace('-', '')))

### Set zipcode as the index
tokyo.set_index('zipcode', inplace=True)

tokyo.head()

Country_code State_province county_district  area      sub_area  \
zipcode                                                                   
1200001           JP      Toukyouto        Adachiku   NaN        Ooyata   
1200002           JP      Toukyouto        Adachiku   NaN      Nakagawa   
1200003           JP      Toukyouto        Adachiku   NaN         Touwa   
1200004           JP      Toukyouto        Adachiku   NaN  Higashiayase   
1200005           JP      Toukyouto        Adachiku   NaN         Ayase   

             lat       lng  
zipcode                     
1200001  35.7805  139.8421  
1200002  35.7704  139.8518  
1200003  35.7709  139.8400  
1200004  35.7668  139.8325  
1200005  35.7644  139.8255

In [3]:
### Download zipcodes data

zipcodes_zip = 'http://www.post.japanpost.jp/zipcode/dl/oogaki/zip/13tokyo.zip'

if not os.path.exists('../data/tokyo_zipcodes/13TOKYO.CSV'):
    r = requests.get('http://www.post.japanpost.jp/zipcode/dl/oogaki/zip/13tokyo.zip')
    with open('/tmp/tokyo_zipcodes.zip', 'wb') as f: 
        f.write(r.content)
    z = zipfile.ZipFile('/tmp/tokyo_zipcodes.zip')
    z.extractall('../data/tokyo_zipcodes')
    
    
tokyo_zipcodes = pd.read_csv('../data/tokyo_zipcodes/13TOKYO.CSV', encoding = 'shift-jis')
tokyo_zipcodes.rename(columns = {'1000000': 'zipcode'}, inplace=True)
tokyo_zipcodes.drop(['13101', '100  ', '0', '0.1', '0.2', '0.3', '0.4', '0.5'], axis=1, inplace=True)
tokyo_zipcodes.set_index('zipcode', inplace=True)
tokyo_zipcodes.head()


ﾄｳｷﾖｳﾄ  ﾁﾖﾀﾞｸ ｲｶﾆｹｲｻｲｶﾞﾅｲﾊﾞｱｲ  東京都  千代田区 以下に掲載がない場合
zipcode                                                     
1020072  ﾄｳｷﾖｳﾄ  ﾁﾖﾀﾞｸ         ｲｲﾀﾞﾊﾞｼ  東京都  千代田区        飯田橋
1020082  ﾄｳｷﾖｳﾄ  ﾁﾖﾀﾞｸ        ｲﾁﾊﾞﾝﾁﾖｳ  東京都  千代田区        一番町
1010032  ﾄｳｷﾖｳﾄ  ﾁﾖﾀﾞｸ         ｲﾜﾓﾄﾁﾖｳ  東京都  千代田区        岩本町
1010047  ﾄｳｷﾖｳﾄ  ﾁﾖﾀﾞｸ          ｳﾁｶﾝﾀﾞ  東京都  千代田区        内神田
1000011  ﾄｳｷﾖｳﾄ  ﾁﾖﾀﾞｸ       ｳﾁｻｲﾜｲﾁﾖｳ  東京都  千代田区        内幸町

In [4]:
data = pd.read_table('query_areas.txt', dtype={'zipcode': str})

data.head()

northlatitude  eastlongitude  zipcode  review_count  total_score_ave  \
0      43.053838     141.357369  0600063            97             3.53   
1      43.051056     141.358429  0640806            47             3.95   
2      43.054637     141.319532  0600001           178             3.83   
3      43.054073     141.357641  0600063            52             3.83   
4      43.055611     141.315868  0640959           141             3.94   

  area3_name  
0       すすきの  
1     豊水すすきの  
2       円山公園  
3       すすきの  
4      西２８丁目

In [5]:
### Remove restaurants with no zipcode
data = data[data.zipcode.notnull()]

### Create mapping from zipcode to ku
zip_ku = tokyo['county_district'].loc[data.zipcode]

### Set zipcode as index
data.set_index('zipcode', inplace=True)

### Add zip to ku mapping to dataframe
data = data.assign(ku = zip_ku)

### Remove restaurants that are not in any of the zipcodes in Tokyo
data = data[data.ku.notnull()]

### lowercase ward names
data.ku = data.ku.map(lambda k: k.lower())

data.head()

northlatitude  eastlongitude  review_count  total_score_ave  \
zipcode                                                                
1070052      35.672116     139.735773           103             3.55   
1030013      35.681148     139.787445           117             3.42   
1060032      35.656483     139.731817           244             3.36   
1060032      35.656485     139.731818             3             3.83   
1060032      35.656484     139.731818            63             3.31   

        area3_name        ku  
zipcode                       
1070052       赤坂見附  minatoku  
1030013       水天宮前  chuuouku  
1060032        六本木  minatoku  
1060032        六本木  minatoku  
1060032        六本木  minatoku

Grouping by ku and calculating feature averages for each zipcode

In [6]:
stats = data.groupby('ku').aggregate([np.mean, np.std, np.median, 'count'])

### Nasty hack to rename long o's to short o's (e.g. bunkyouku to bunkyoku)
stats.index = stats.index.map(lambda x: x.replace('ou', 'o'))

In [7]:
stats[['review_count', 'total_score_ave']].sort_values(by=('review_count', 'mean'), ascending=False).head()

review_count                          total_score_ave            \
                   mean        std median  count            mean       std   
ku                                                                           
shibuyaku     25.308388  50.934107    9.0  11385        2.776717  1.196797   
chuuoku       25.131996  51.983253    9.0  11864        2.826659  1.152428   
chiyodaku     24.035942  53.625357    9.0  10350        2.730418  1.123902   
minatoku      23.315874  44.733496    9.0  15006        2.846098  1.139281   
shinjukuku    20.774279  43.805268    7.0  12768        2.760488  1.186556   

                          
           median  count  
ku                        
shibuyaku    3.15  11385  
chuuoku      3.17  11864  
chiyodaku    3.08  10350  
minatoku     3.16  15006  
shinjukuku   3.12  12768

In [8]:
### Load wards geojson data, or download if not already on disk
if not os.path.exists('tokyo_wards.geojson'):
    r = requests.get('https://raw.githubusercontent.com/dataofjapan/land/master/tokyo.geojson')
    wards = json.loads(r.content.decode())
    with open('tokyo_wards.geojson', 'w') as f:
        f.write(json.dumps(wards))
else:         
    with open('tokyo_wards.geojson') as f: 
        wards = json.loads(f.read())

    

In [9]:
### Read wards in geopandas dataframe
wards = gpd.GeoDataFrame.from_file('tokyo_wards.geojson')
print('Dropping rows {}'.format(wards[wards.isnull().any(1)]))
wards.dropna(inplace=True)
tmp = wards.ward_en.map(lambda w: w.replace(' ', '').lower())
wards['ward_en'] = tmp
wards.set_index('ward_en', inplace=True)
wards.head()

Dropping rows Empty GeoDataFrame
Columns: [area_en, area_ja, code, geometry, ward_en, ward_ja]
Index: []


area_en area_ja    code  \
ward_en                               
adachiku     Tokubu     都区部  131211   
bunkyoku     Tokubu     都区部  131059   
chiyodaku    Tokubu     都区部  131016   
taitoku      Tokubu     都区部  131067   
shinagawaku  Tokubu     都区部  131091   

                                                      geometry ward_ja  
ward_en                                                                 
adachiku     POLYGON ((139.821051 35.815077, 139.821684 35....     足立区  
bunkyoku     POLYGON ((139.760933 35.732206, 139.761002 35....     文京区  
chiyodaku    POLYGON ((139.770135 35.705352, 139.770172 35....    千代田区  
taitoku      POLYGON ((139.809714 35.728135, 139.809705 35....     台東区  
shinagawaku  (POLYGON ((139.719199 35.641847, 139.719346 35...     品川区

In [10]:

### Adding statistics columns to wards dataframe
wards['score_mean'] = stats.loc[wards.index][('total_score_ave', 'mean')]
wards.dropna(inplace=True)
wards.head()


area_en area_ja    code  \
ward_en                               
adachiku     Tokubu     都区部  131211   
bunkyoku     Tokubu     都区部  131059   
chiyodaku    Tokubu     都区部  131016   
taitoku      Tokubu     都区部  131067   
shinagawaku  Tokubu     都区部  131091   

                                                      geometry ward_ja  \
ward_en                                                                  
adachiku     POLYGON ((139.821051 35.815077, 139.821684 35....     足立区   
bunkyoku     POLYGON ((139.760933 35.732206, 139.761002 35....     文京区   
chiyodaku    POLYGON ((139.770135 35.705352, 139.770172 35....    千代田区   
taitoku      POLYGON ((139.809714 35.728135, 139.809705 35....     台東区   
shinagawaku  (POLYGON ((139.719199 35.641847, 139.719346 35...     品川区   

             score_mean  
ward_en                  
adachiku       2.724882  
bunkyoku       2.819527  
chiyodaku      2.730418  
taitoku        2.694437  
shinagawaku    2.764723

In [11]:
ward_dict = wards['score_mean']
ward_dict.sort_index(inplace=True)
ward_dict.head()

ward_en
adachiku       2.724882
akirunoshi     2.676275
akishimashi    2.759405
arakawaku      2.690501
bunkyoku       2.819527
Name: score_mean, dtype: float64

In [12]:
from branca.colormap import linear

colormap = linear.OrRd.scale(
    wards.score_mean.min(),
    wards.score_mean.max())

print(colormap(5.0))

colormap

#990000


In [13]:
colors = wards['score_mean'].apply(colormap)

In [14]:
m = folium.Map(location=[35.7035007,139.6524644], tiles='Stamen Toner',
                    zoom_start=11)

folium.GeoJson(
    wards.to_json(),
    style_function=lambda feature: {
        'fillColor': colors.loc[feature['id']],
        'color': 'black',
        'weight': 1,
        'dashArray': '5, 5',
        'fillOpacity': 0.9,
        'highlight': True
    }
).add_to(m)

folium.LayerControl().add_to(m)
#folium.LayerControl().add_to(m)
m

In [15]:
from folium.features import DivIcon
m = folium.Map(location=[35.7035007,139.6524644], tiles='Stamen Toner',
                    zoom_start=11)

g = folium.GeoJson(
    wards.to_json(),
    style_function=lambda feature: {
        'fillColor': colormap(ward_dict.loc[feature['id']]),
        'color': 'black',
        'weight': 1,
        'dashArray': '5, 5',
        'fillOpacity': 0.9,
    }
).add_to(m)


for centroid in wards.geometry.centroid:
    print(centroid)

folium.map.Marker(
    wards.geometry.centroid.iloc[0],
    icon=DivIcon(
        icon_size=(150,36),
        icon_anchor=(0,0),
        html='<div style="font-size: 12pt">中野区</div>',
        )
    ).add_to(m)
m

POINT (139.7950785011842 35.77880814302382)
POINT (139.7472814598948 35.71745659551482)
POINT (139.75468090087 35.68763927885675)
POINT (139.7859837688935 35.71548269547309)
POINT (139.7335467169758 35.60970420486629)
POINT (139.8756661100966 35.69242063763337)
POINT (139.7089716172202 35.70106882346283)
POINT (139.696273592214 35.66788396562983)
POINT (139.7289174235783 35.76589868776492)
POINT (139.7116302943617 35.73152916225538)
POINT (139.6254207699834 35.69681138253885)
POINT (139.6764611065892 35.77257558933155)
POINT (139.635070261667 35.63971064196735)
POINT (139.8154717713145 35.71221018305685)
POINT (139.6624724769075 35.71091848602059)
POINT (139.6176679628409 35.74784910249625)
POINT (139.8142850834332 35.65939813936206)
POINT (139.6882301788956 35.62997351937271)
POINT (139.8556668891101 35.75324861056951)
POINT (139.7397457140871 35.65149154153657)
POINT (139.7812867774363 35.73993184759643)
POINT (139.5521821188418 35.6576853156909)
POINT (139.4045224220399 35.714476563

In [16]:
from jinja2 import Template    
m = folium.Map(location=[35.7035007,139.6524644], tiles='Stamen Toner',
                    zoom_start=11)

g = folium.GeoJson(
    wards.to_json(),
    style_function=lambda feature: {
        'fillColor': colormap(ward_dict.loc[feature['id']]),
        'color': 'black',
        'weight': 1,
        'dashArray': '5, 5',
        'fillOpacity': 0.9,
    }
).add_to(m)

folium.LayerControl().add_to(m)

g._template = Template("""
            {% macro script(this, kwargs) %}
               var {{this.get_name()}} = {};                
               
               var html_aaa = $('<div id="html_aaa" style="width: 100.0%; height: 100.0%;">Asir</div>')[0];
                //var data = 
               //{{this.get_name()}}.onEachFeature = function onEachFeature(f){return f.properties.ward_ja;};                
               //popup_aaa.setContent({{this.get_name()}}.onEachFeature = function(feature){return feature.properties.ward_ja})
               //{"properties": {"area_ja": "\\u90fd\\u533a\\u90e8", "area_en": "Tokubu", "code": 131091.0, "ward_ja": "\\u54c1\\u5ddd\\u533a", "score_mean": 2.9428980013783588}, "id": "shinagawaku"}));
                
                {{this.get_name()}}.style = function(feature) {return feature.properties.style;};
                
                
                
                {{this.get_name()}}.highlightStyle = function(feature) {return {
                        weight: 2,
                        color: '#666',
                        dashArray: '',
                        fillOpacity: 0.7
                        };
                    };
                {{this.get_name()}}.onEachFeature = function onEachFeature(feature, layer) {
                    layer.on({
                        mouseover: function(e) {
                            e.target.setStyle({{this.get_name()}}.highlightStyle(e.target.feature));
                            e.target.bindPopup(popup_aaa);},
                        mouseout: function(e) {
                            {{this.get_name()}}.geoJson.resetStyle(e.target);
                            }
                        });
                        console.log(feature.properties.ward_ja);
                        var popup_aaa = L.popup({maxWidth: '300'});
                        popup_aaa.setContent(feature.properties.ward_ja);
                    };
                    
                    
                    
                    
                {{this.get_name()}}.geoJson = L.geoJson(
                    {% if this.embed %}{{this.style_data()}}{% else %}"{{this.data}}"{% endif %},{
                        style : {{this.get_name()}}.style,
                        onEachFeature: {{this.get_name()}}.onEachFeature
                        })
                    .addTo({{this._parent.get_name()}});
            {% endmacro %}
""")    

# # And draw the map with additions, save
# m.add_child(g)
# m.add_child(colormap)

m.save('shit.html')
m

In [29]:

with open('wards2.geojson', 'w') as f:
    f.write(wards.to_json())
    
m = folium.Map(location=[35.7035007,139.6524644], zoom_start=11)

m.choropleth(
    geo_path='wards2.geojson',
    key_on='feature.id',
    fill_color='OrRd',
    fill_opacity=0.3,
    line_opacity=1,
    line_weight=3,
    legend_name='Unemployment Rate (%)',
    highlight=True
)
m
m.save('pyconjp2017/html/wards_boundaries.html')

In [18]:
.

SyntaxError: invalid syntax (<ipython-input-18-8cf8463b34ca>, line 1)